In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm_notebook
from scipy import stats
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.metrics import roc_auc_score

In [2]:
data = pd.read_csv('Berlin-AudioData.csv')
data.head()

mfcc0      mfcc1      mfcc2      mfcc3      mfcc4      mfcc5  \
0 -233.65387   98.92121 -52.956680  45.900646 -22.164831  23.607706   
1 -269.85010  101.00359 -20.072445  31.245241 -16.867949  12.147052   
2 -245.53682   80.80759 -61.844658  56.772570 -31.858640  -4.545132   
3 -267.13180   67.51291 -70.434204  34.460457 -39.655160  16.993803   
4 -242.85654   69.06733 -48.731880  40.928734 -41.087864  11.601104   

       mfcc6      mfcc7      mfcc8      mfcc9  ...     mfcc11    mfcc12  \
0 -23.457792   8.316013 -12.720743  -6.341973  ...  -6.935918 -3.001800   
1 -15.716954   2.299682 -17.418932  -4.849804  ...  -6.856007 -3.841342   
2 -25.359083 -16.917744 -13.844658  -6.528104  ...  -5.345687 -2.694414   
3 -30.940466  -1.460678 -10.892535 -10.028064  ...  -4.080286  0.601137   
4 -13.702060  -7.561162 -11.418545 -12.069065  ... -10.181156 -3.369477   

      mfcc13     mfcc14     mfcc15    mfcc16     mfcc17    mfcc18    mfcc19  \
0 -12.712770  14.264772 -14.044920 -1.110774  -3.902819 -0.631407 -0.875262   
1  -3.725923  10.107684 -11.766808  3.667881  -2.547494  1.900528  2.074626   
2 -11.347428  -4.289738 -18.830544  9.611272 -12.124508  3.009437  5.802058   
3 -17.285723  10.771420  -8.910603 -3.997675  -3.068863  1.155385 -5.617516   
4  -2.071053   3.297643  -8.978094  1.416900  -4.287317  2.396644  2.252754   

   Emotion  
0        5  
1        5  
2        1  
3        1  
4        1  

[5 rows x 21 columns]

In [3]:
data.shape

(535, 21)

In [3]:
y = data.iloc[:, -1: ]
x = data.iloc[:, 0: -1]
x.shape, y.shape

((535, 20), (535, 1))

In [6]:
x

mfcc0       mfcc1      mfcc2      mfcc3      mfcc4      mfcc5  \
0   -233.65387   98.921210 -52.956680  45.900646 -22.164831  23.607706   
1   -269.85010  101.003590 -20.072445  31.245241 -16.867949  12.147052   
2   -245.53682   80.807590 -61.844658  56.772570 -31.858640  -4.545132   
3   -267.13180   67.512910 -70.434204  34.460457 -39.655160  16.993803   
4   -242.85654   69.067330 -48.731880  40.928734 -41.087864  11.601104   
..         ...         ...        ...        ...        ...        ...   
530 -230.84317  118.376990 -13.599730  33.739280 -27.688364  18.706244   
531 -243.78563  108.967606  -2.422872  59.694040 -14.385405  24.197319   
532 -313.61737   93.710940  14.021646  41.269726   7.971857  24.996262   
533 -255.58336  130.778850 -28.694363  66.970215 -17.989250  29.417858   
534 -338.21655   37.868187 -69.146750  49.080948 -33.890007   3.932854   

         mfcc6      mfcc7      mfcc8      mfcc9     mfcc10     mfcc11  \
0   -23.457792   8.316013 -12.720743  -6.341973   1.201577  -6.935918   
1   -15.716954   2.299682 -17.418932  -4.849804   0.615920  -6.856007   
2   -25.359083 -16.917744 -13.844658  -6.528104 -19.150093  -5.345687   
3   -30.940466  -1.460678 -10.892535 -10.028064  -5.231388  -4.080286   
4   -13.702060  -7.561162 -11.418545 -12.069065  -4.819385 -10.181156   
..         ...        ...        ...        ...        ...        ...   
530 -11.750737  -2.126415 -10.853242  -6.937043  -4.498544  -4.099695   
531  -9.769530  -9.844581  -9.557492  -9.040439   2.274538 -10.305232   
532  -3.107922   8.484037   3.339436  -2.026417   5.469033   0.722273   
533  -3.517510  10.482176 -12.653866  -3.661761   2.260246   0.562704   
534 -25.879818  -5.768258 -15.095667 -10.199753  -4.631788  -9.788631   

       mfcc12     mfcc13     mfcc14     mfcc15     mfcc16     mfcc17  \
0   -3.001800 -12.712770  14.264772 -14.044920  -1.110774  -3.902819   
1   -3.841342  -3.725923  10.107684 -11.766808   3.667881  -2.547494   
2   -2.694414 -11.347428  -4.289738 -18.830544   9.611272 -12.124508   
3    0.601137 -17.285723  10.771420  -8.910603  -3.997675  -3.068863   
4   -3.369477  -2.071053   3.297643  -8.978094   1.416900  -4.287317   
..        ...        ...        ...        ...        ...        ...   
530 -4.275291  -7.805464   9.989097 -15.326363  -0.945981  -3.454961   
531 -3.047161   3.729689   8.782693  -4.205489  -0.530832  -4.670637   
532  0.661930   8.333894   9.390378  -6.911213   3.484412  -1.643400   
533  5.806162  -9.980883  14.386482  -8.226897   2.629791  -4.504953   
534 -3.788358   7.402183  21.856033  -0.213831  22.232962   5.789885   

       mfcc18    mfcc19  
0   -0.631407 -0.875262  
1    1.900528  2.074626  
2    3.009437  5.802058  
3    1.155385 -5.617516  
4    2.396644  2.252754  
..        ...       ...  
530 -5.578834 -4.343633  
531 -4.965991 -6.890536  
532 -1.400049 -1.828547  
533 -0.264485  0.102751  
534  6.515108  6.723586  

[535 rows x 20 columns]

In [7]:
y

Emotion
0          5
1          5
2          1
3          1
4          1
..       ...
530        7
531        2
532        6
533        7
534        5

[535 rows x 1 columns]

In [5]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size= 0.3, random_state=42)

In [6]:
x_train.shape, x_test.shape, y_train.shape, y_test.shape

((374, 20), (161, 20), (374, 1), (161, 1))

In [7]:
features = [f'mfcc{i}' for i in range(20)]
features

['mfcc0',
 'mfcc1',
 'mfcc2',
 'mfcc3',
 'mfcc4',
 'mfcc5',
 'mfcc6',
 'mfcc7',
 'mfcc8',
 'mfcc9',
 'mfcc10',
 'mfcc11',
 'mfcc12',
 'mfcc13',
 'mfcc14',
 'mfcc15',
 'mfcc16',
 'mfcc17',
 'mfcc18',
 'mfcc19']

In [8]:
from sklearn.preprocessing import StandardScaler

scale = StandardScaler()

scale.fit(x_train[features])

StandardScaler()

In [9]:
train = scale.transform(x_train[features])
test = scale.transform(x_test[features])
test

array([[ 0.83051692,  0.61920272,  0.01636521, ..., -0.07407429,
         0.58425698, -0.62617124],
       [-0.96839227,  1.29538096,  1.34272465, ...,  0.39622824,
         0.60323595, -0.0584341 ],
       [ 0.13551165,  1.59860326, -0.62956958, ..., -0.23014348,
        -0.61568941,  0.08658033],
       ...,
       [ 0.75462646, -0.42259916,  0.15325003, ..., -0.69755061,
         0.13370932,  0.07259667],
       [ 0.28352041, -0.20411953,  0.16241872, ..., -0.74047456,
         0.47084663, -0.41053189],
       [ 0.15706664, -0.63967219, -1.11509583, ..., -2.82572668,
        -0.45065053, -0.22656509]])

In [11]:
len(train[0]), len(test[0])

(20, 20)

In [10]:
x_train = pd.DataFrame(train, columns= features)
x_test = pd.DataFrame(test, columns= features)
x_train.shape, x_test.shape

((374, 20), (161, 20))

In [13]:
from sklearn import metrics

In [14]:
def EvaluateModel(y_test, y_pred, y_pred_preba, label):
    print("Accuracy:",metrics.accuracy_score(y_test, y_pred))
    
    print("Precision:",metrics.precision_score(y_test, y_pred, average='weighted'))

    print("Recall:",metrics.recall_score(y_test, y_pred, average='weighted'))

    print("AUC Score:",roc_auc_score(y_test.values.ravel(), y_pred_proba, average='macro', multi_class='ovo'))

In [13]:
from sklearn import svm

SVM = svm.SVC(verbose=True, probability = True)

SVM.fit(x_train, y_train.values.ravel())

[LibSVM]*
optimization finished, #iter = 111
obj = -12.919682, rho = 0.115932
nSV = 51, nBSV = 10
Total nSV = 51
*.*
optimization finished, #iter = 119
obj = -12.853397, rho = 0.172596
nSV = 52, nBSV = 8
Total nSV = 52
*
optimization finished, #iter = 116
obj = -12.336798, rho = 0.122616
nSV = 52, nBSV = 8
Total nSV = 52
*
optimization finished, #iter = 112
obj = -12.473510, rho = 0.160669
nSV = 53, nBSV = 9
Total nSV = 53
*.*
optimization finished, #iter = 123
obj = -11.219644, rho = 0.176670
nSV = 51, nBSV = 5
Total nSV = 51
*
optimization finished, #iter = 131
obj = -13.444888, rho = -0.163564
nSV = 57, nBSV = 9
*.*
optimization finished, #iter = 106
obj = -16.902308, rho = 0.275922
nSV = 49, nBSV = 15
Total nSV = 49
*
optimization finished, #iter = 89
obj = -17.539144, rho = 0.306758
nSV = 56, nBSV = 16
Total nSV = 56
*
optimization finished, #iter = 83
obj = -17.540682, rho = 0.260588
nSV = 50, nBSV = 17
Total nSV = 50
*
optimization finished, #iter = 94
obj = -17.314045, rho = 0.

SVC(probability=True, verbose=True)

In [15]:
y_pred = SVM.predict(x_test)
y_pred_proba = SVM.predict_proba(x_test)
y_pred

array([4, 6, 7, 4, 4, 5, 1, 1, 1, 2, 5, 7, 2, 1, 7, 4, 7, 7, 1, 5, 7, 1,
       2, 6, 1, 4, 5, 1, 2, 7, 2, 6, 1, 7, 1, 4, 7, 2, 3, 1, 1, 4, 4, 4,
       1, 1, 1, 2, 1, 4, 2, 6, 1, 6, 7, 4, 6, 2, 7, 2, 1, 1, 7, 6, 1, 7,
       1, 2, 1, 1, 7, 3, 1, 5, 6, 6, 2, 2, 2, 2, 1, 1, 4, 7, 5, 1, 1, 6,
       1, 2, 1, 6, 4, 4, 5, 5, 7, 1, 7, 4, 4, 7, 4, 1, 4, 5, 2, 2, 1, 2,
       2, 3, 3, 7, 7, 2, 1, 3, 6, 7, 1, 2, 7, 6, 5, 1, 3, 1, 6, 5, 1, 4,
       4, 1, 6, 3, 5, 2, 6, 1, 1, 1, 6, 1, 1, 6, 7, 5, 3, 6, 6, 7, 5, 1,
       5, 6, 1, 4, 4, 4, 1])

In [16]:
y_test.values.ravel().shape

(161,)

In [17]:
y_pred_proba.shape

(161, 7)

In [18]:
EvaluateModel(y_test, y_pred, y_pred_proba, "SVM")

Accuracy: 0.7391304347826086
Precision: 0.7401889292096197
Recall: 0.7391304347826086
AUC Score: 0.962637487965285


In [ ]:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from scipy import stats
rand_list = {"C": stats.uniform(2, 10),
             "gamma": stats.uniform(0.1, 1),
             "kernel": ['linear', 'rbf']
            }
SVM = svm.SVC(verbose=True, probability = True)
SVM_tuned = RandomizedSearchCV(SVM, param_distributions = rand_list, n_iter = 40, cv = 10, scoring = 'roc_auc_ovo', verbose=True)
SVM_tuned.fit(x_train, y_train.values.ravel())
SVM_best_params = SVM_tuned.best_params_
SVM_best_params["verbose"] = True
# SVM_best_params["n_jobs"] = -1
SVM_best_params

Fitting 10 folds for each of 40 candidates, totalling 400 fits
[LibSVM].*.*
optimization finished, #iter = 255
obj = -49.558925, rho = 0.218349
nSV = 105, nBSV = 0
Total nSV = 105
..*
optimization finished, #iter = 275
obj = -50.397285, rho = 0.179235
nSV = 105, nBSV = 0
Total nSV = 105
..*
optimization finished, #iter = 281
obj = -50.363491, rho = 0.179743
nSV = 105, nBSV = 0
Total nSV = 105
.*.*
optimization finished, #iter = 225
obj = -49.085305, rho = 0.232866
nSV = 105, nBSV = 0
Total nSV = 105
..*
optimization finished, #iter = 267
obj = -50.461673, rho = 0.132261
nSV = 104, nBSV = 0
Total nSV = 104
.*.*
optimization finished, #iter = 331
obj = -62.408270, rho = -0.187565
nSV = 131, nBSV = 0
.*.*
optimization finished, #iter = 207
obj = -35.676292, rho = 0.434097
nSV = 89, nBSV = 0
Total nSV = 89
..*.*
optimization finished, #iter = 271
obj = -37.405212, rho = 0.388351
nSV = 89, nBSV = 0
Total nSV = 89
.*.*
optimization finished, #iter = 204
obj = -35.674062, rho = 0.435472
nSV =

In [20]:
SVM_best_params

{'C': 3.7969288813151483,
 'gamma': 0.16620415688221749,
 'kernel': 'rbf',
 'verbose': True}

In [23]:
SVM_new = svm.SVC(**SVM_best_params, probability = True)

SVM_new.fit(x_train, y_train.values.ravel())
y_pred = SVM_new.predict(x_test)
y_pred_proba = SVM_new.predict_proba(x_test)
print("After Hyper-Parameter Tuning: ")
EvaluateModel(y_test, y_pred, y_pred_proba, "SVM New")

[LibSVM].*
optimization finished, #iter = 197
obj = -25.578275, rho = 0.178413
nSV = 107, nBSV = 0
Total nSV = 107
.*
optimization finished, #iter = 205
obj = -25.717640, rho = 0.201638
nSV = 108, nBSV = 0
Total nSV = 108
.*
optimization finished, #iter = 202
obj = -25.343044, rho = 0.192612
nSV = 106, nBSV = 0
Total nSV = 106
.*
optimization finished, #iter = 211
obj = -25.525690, rho = 0.123779
nSV = 110, nBSV = 0
Total nSV = 110
.*
optimization finished, #iter = 196
obj = -25.332022, rho = 0.151373
nSV = 105, nBSV = 0
Total nSV = 105
.*
optimization finished, #iter = 248
obj = -28.536591, rho = -0.175752
nSV = 126, nBSV = 0
.*
optimization finished, #iter = 182
obj = -22.518136, rho = 0.370995
nSV = 92, nBSV = 0
Total nSV = 92
.*
optimization finished, #iter = 161
obj = -20.804821, rho = 0.451350
nSV = 89, nBSV = 0
Total nSV = 89
.*
optimization finished, #iter = 177
obj = -22.109349, rho = 0.374878
nSV = 89, nBSV = 0
Total nSV = 89
.*
optimization finished, #iter = 181
obj = -21.53

In [15]:
from sklearn.ensemble import RandomForestClassifier

RandForest = RandomForestClassifier(verbose= True, n_jobs= - 1)
RandForest.fit(x_train, y_train.values.ravel())
y_pred_forest = RandForest.predict(x_test)
y_pred_proba = RandForest.predict_proba(x_test)

print('\nBefore Hyper-Parameter Tuning: ')
EvaluateModel(y_test, y_pred_forest, y_pred_proba, "RandomForest")


Before Hyper-Parameter Tuning: 
Accuracy: 0.6583850931677019
Precision: 0.6458280969488098
Recall: 0.6583850931677019
AUC Score: 0.940715177483097


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.0s finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 100 out of 100 | elapsed:    0.0s finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 100 out of 100 | elapsed:    0.0s finished


In [22]:
np.arange(10, 510, 10)

array([ 10,  20,  30,  40,  50,  60,  70,  80,  90, 100, 110, 120, 130,
       140, 150, 160, 170, 180, 190, 200, 210, 220, 230, 240, 250, 260,
       270, 280, 290, 300, 310, 320, 330, 340, 350, 360, 370, 380, 390,
       400, 410, 420, 430, 440, 450, 460, 470, 480, 490, 500])

In [17]:
import time

In [20]:
start = time.time()
rf_p_dist={'max_depth':[10, 20, 30, 40, 50, 60, 70, 80, 90, 100, None],
              'n_estimators':np.arange(10, 510, 10),
              'max_features':np.arange(0.05, 1, 0.05),
               'criterion':['gini','entropy'],
               'bootstrap':[True,False],
               'min_samples_leaf':np.arange(0.05, 1, 0.05),
              }
RandForest = RandomForestClassifier(verbose= True, n_jobs= - 1)
rf_tuned = RandomizedSearchCV(RandForest, param_distributions= rf_p_dist, n_iter = 50, cv = 20, scoring = 'roc_auc_ovo',n_jobs= -1, verbose=True)
rf_tuned.fit(x_train, y_train.values.ravel())
rf_best_params = rf_tuned.best_params_
rf_best_params["verbose"] = True
rf_best_params["n_jobs"] = -1
end = time.time()
print('Total Time to Execute:', (end - start) / 60, ' Min')
print(rf_best_params)

Fitting 20 folds for each of 50 candidates, totalling 1000 fits


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:    0.2s


Total Time to Execute: 2.7088082154591877  Min
{'n_estimators': 380, 'min_samples_leaf': 0.05, 'max_features': 0.1, 'max_depth': 60, 'criterion': 'gini', 'bootstrap': False, 'verbose': True, 'n_jobs': -1}


[Parallel(n_jobs=-1)]: Done 380 out of 380 | elapsed:    0.5s finished


In [21]:
RandForest = RandomForestClassifier(**rf_best_params)
RandForest.fit(x_train, y_train.values.ravel())
y_pred_forest_new = RandForest.predict(x_test)
y_pred_proba = RandForest.predict_proba(x_test)

print('\nAfter Hyper-Parameter Tuning: ')
EvaluateModel(y_test, y_pred_forest_new, y_pred_proba, "RandomForest")

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:    0.2s
[Parallel(n_jobs=-1)]: Done 380 out of 380 | elapsed:    0.6s finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 184 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 380 out of 380 | elapsed:    0.1s finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.



After Hyper-Parameter Tuning: 
Accuracy: 0.6211180124223602
Precision: 0.6372919640445971
Recall: 0.6211180124223602
AUC Score: 0.9222925392724345


[Parallel(n_jobs=8)]: Done  34 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 184 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 380 out of 380 | elapsed:    0.1s finished


In [15]:
from sklearn.neural_network import MLPClassifier

mlp = MLPClassifier(hidden_layer_sizes=[30], batch_size= 16, learning_rate_init=0.001, verbose=True)

mlp.fit(x_train, y_train.values.ravel())
y_pred = mlp.predict(x_test)
y_pred_proba = mlp.predict_proba(x_test)
print('----------------------------Before Hyper-Parameter Tuning------------------------------------')
EvaluateModel(y_test, y_pred, y_pred_proba, label = "ANN")

Iteration 1, loss = 2.20104141
Iteration 2, loss = 1.87456950
Iteration 3, loss = 1.65571931
Iteration 4, loss = 1.50083267
Iteration 5, loss = 1.37984136
Iteration 6, loss = 1.28843527
Iteration 7, loss = 1.21404278
Iteration 8, loss = 1.15206953
Iteration 9, loss = 1.09967203
Iteration 10, loss = 1.05406497
Iteration 11, loss = 1.01417538
Iteration 12, loss = 0.97727422
Iteration 13, loss = 0.94380020
Iteration 14, loss = 0.91455823
Iteration 15, loss = 0.88557128
Iteration 16, loss = 0.85982923
Iteration 17, loss = 0.83551534
Iteration 18, loss = 0.81304382
Iteration 19, loss = 0.79184690
Iteration 20, loss = 0.77092156
Iteration 21, loss = 0.75332961
Iteration 22, loss = 0.73470772
Iteration 23, loss = 0.71807113
Iteration 24, loss = 0.70186031
Iteration 25, loss = 0.68795836
Iteration 26, loss = 0.67442431
Iteration 27, loss = 0.66118573
Iteration 28, loss = 0.64916434
Iteration 29, loss = 0.63685970
Iteration 30, loss = 0.62531614
Iteration 31, loss = 0.61587788
Iteration 32, los

C:\Users\pgupt\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


In [17]:
mlp_params = {
    'hidden_layer_sizes' : [[i] for i in range(10, 50, 10)] + [[i, i//2] for i in range(10, 50, 10)],
    'activation': ['identity', 'logistic', 'tanh', 'relu'],
    'solver': ['lbfgs', 'sgd', 'adam'],
    'alpha': stats.uniform(0, 0.01),
    'batch_size': [8, 16, 32, 64],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
    'learning_rate_init': stats.uniform(0.00001,0.1),
    'max_iter': [i for i in range(100, 500, 50)]
}
mlp_params

{'hidden_layer_sizes': [[10],
  [20],
  [30],
  [40],
  [10, 5],
  [20, 10],
  [30, 15],
  [40, 20]],
 'activation': ['identity', 'logistic', 'tanh', 'relu'],
 'solver': ['lbfgs', 'sgd', 'adam'],
 'alpha': <scipy.stats._distn_infrastructure.rv_frozen at 0x2264e406e90>,
 'batch_size': [8, 16, 32, 64],
 'learning_rate': ['constant', 'invscaling', 'adaptive'],
 'learning_rate_init': <scipy.stats._distn_infrastructure.rv_frozen at 0x22650793df0>,
 'max_iter': [100, 150, 200, 250, 300, 350, 400, 450]}

In [18]:
mlp_params = {
    'hidden_layer_sizes' : [[i] for i in range(10, 50, 10)] + [[i, i//2] for i in range(10, 50, 10)],
    'activation': ['identity', 'logistic', 'tanh', 'relu'],
    'solver': ['lbfgs', 'sgd', 'adam'],
    'alpha': stats.uniform(0, 0.01),
    'batch_size': [8, 16, 32, 64],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
    'learning_rate_init': stats.uniform(0.00001,0.1),
    'max_iter': [i for i in range(100, 500, 50)]
}
MLP = RandomizedSearchCV(estimator= mlp, param_distributions= mlp_params, cv= 40, n_iter= 10, scoring='roc_auc_ovo', n_jobs = -1, verbose= True)
MLP.fit(x_train, y_train.values.ravel())
MLP_best_params = MLP.best_params_
MLP_best_params["verbose"] = True
MLP_best_params

Fitting 40 folds for each of 10 candidates, totalling 400 fits


C:\Users\pgupt\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\model_selection\_split.py:680: UserWarning: The least populated class in y has only 37 members, which is less than n_splits=40.
  warnings.warn(
C:\Users\pgupt\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\model_selection\_search.py:953: UserWarning: One or more of the test scores are non-finite: [nan nan nan nan nan nan nan nan nan nan]
  warnings.warn(


Iteration 1, loss = 2.43343344
Iteration 2, loss = 2.39464664
Iteration 3, loss = 0.95193338
Iteration 4, loss = 0.76210307
Iteration 5, loss = 0.72088804
Iteration 6, loss = 0.68066832
Iteration 7, loss = 0.66841183
Iteration 8, loss = 0.66014109
Iteration 9, loss = 0.64890360
Iteration 10, loss = 0.62509312
Iteration 11, loss = 0.62826042
Iteration 12, loss = 0.62432661
Iteration 13, loss = 0.61361323
Iteration 14, loss = 0.60826346
Iteration 15, loss = 0.60251877
Iteration 16, loss = 0.59809765
Iteration 17, loss = 0.59151347
Iteration 18, loss = 0.58969384
Iteration 19, loss = 0.58342908
Iteration 20, loss = 0.58996295
Iteration 21, loss = 0.58223342
Iteration 22, loss = 0.57849901
Iteration 23, loss = 0.57681751
Iteration 24, loss = 0.57208963
Iteration 25, loss = 0.57166945
Iteration 26, loss = 0.56898587
Iteration 27, loss = 0.56934152
Iteration 28, loss = 0.56246266
Iteration 29, loss = 0.56561807
Iteration 30, loss = 0.56157486
Iteration 31, loss = 0.56124933
Iteration 32, los

C:\Users\pgupt\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


{'activation': 'identity',
 'alpha': 0.0016157426858241153,
 'batch_size': 8,
 'hidden_layer_sizes': [40, 20],
 'learning_rate': 'invscaling',
 'learning_rate_init': 0.07361475357483652,
 'max_iter': 200,
 'solver': 'sgd',
 'verbose': True}

In [28]:
del MLP_best_params['n_jobs']

In [19]:
mlp = MLPClassifier(**MLP_best_params)

mlp.fit(x_train, y_train.values.ravel())
y_pred = mlp.predict(x_test)
y_pred_proba = mlp.predict_proba(x_test)
print('----------------------------After Hyper-Parameter Tuning------------------------------------')
EvaluateModel(y_test, y_pred, y_pred_proba, label = "ANN")

Iteration 1, loss = 1.91073254
Iteration 2, loss = 1.75467253
Iteration 3, loss = 0.94919962
Iteration 4, loss = 0.81683871
Iteration 5, loss = 0.75722233
Iteration 6, loss = 0.71315839
Iteration 7, loss = 0.69274288
Iteration 8, loss = 0.67132560
Iteration 9, loss = 0.65453529
Iteration 10, loss = 0.64938828
Iteration 11, loss = 0.63660415
Iteration 12, loss = 0.62079442
Iteration 13, loss = 0.61473408
Iteration 14, loss = 0.60803518
Iteration 15, loss = 0.61077865
Iteration 16, loss = 0.59969900
Iteration 17, loss = 0.59991571
Iteration 18, loss = 0.59051131
Iteration 19, loss = 0.59244890
Iteration 20, loss = 0.58643158
Iteration 21, loss = 0.58121410
Iteration 22, loss = 0.57792577
Iteration 23, loss = 0.57514566
Iteration 24, loss = 0.57227093
Iteration 25, loss = 0.57194134
Iteration 26, loss = 0.57464931
Iteration 27, loss = 0.57299803
Iteration 28, loss = 0.56490292
Iteration 29, loss = 0.56856687
Iteration 30, loss = 0.56101727
Iteration 31, loss = 0.56065199
Iteration 32, los

C:\Users\pgupt\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:702: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
